In [0]:
from pyspark.sql import SparkSession
from pyspark.sql.functions import *
from pyspark.sql.types import *

spark = SparkSession.builder \
    .appName("Transformação Data Silver") \
    .config("spark.sql.shuffle.partitions", "200")  \
    .config("spark.sql.files.maxPartitionBytes", "128MB") \
    .config("spark.sql.parquet.compression.codec", "snappy") \
    .config("spark.sql.adaptive.enabled", "true") \
    .getOrCreate()

# Define um número fixo de partições para shuffle, melhorando o paralelismo                 
# Define o tamanho máximo de partições para evitar muitos arquivos pequenos        
# Usa o codec Snappy para compressão rápida, otimizando tempo de leitura e escrita    
# Habilita otimizações adaptativas, ajustando o número de partições dinamicamente com base no tamanho dos dados

bronze_path = "/Volumes/workspace/lhdw/bronze/vendas"
silver_path = "/Volumes/workspace/lhdw/silver/vendas"


In [0]:
# Ler dados da camada Bronze
df_bronze = spark.read.format("parquet").load(bronze_path)
#display(df_bronze)

In [0]:
from pyspark.sql.functions import format_number

df_silver = df_bronze.withColumn("Data", to_date(col("Data"), "yyyy-MM-dd")) \
                     .withColumn("Email", lower(expr("regexp_replace(split(EmailNome, ':')[0], '[()]', '')"))) \
                     .withColumn("Nome", expr("split(split(EmailNome, ':')[1], ', ')")) \
                     .withColumn("Nome", expr("concat(Nome[1], ' ', Nome[0])")) \
                     .withColumn("Cidade", expr("split(Cidade, ',')[0]")) \
                     .withColumn("PrecoUnitario", format_number(col("PrecoUnitario").cast("double"), 2)) \
                     .withColumn("CustoUnitario", format_number(col("CustoUnitario").cast("double"), 2)) \
                     .withColumn("TotalVendas", format_number(col("PrecoUnitario").cast("double") * col("Unidades"), 2))\
                     .drop("EmailNome") \
                     .drop("IdCampanha")   
                     

display(df_silver)




IDProduto Data IDCliente Unidades Produto Categoria Segmento IDFabricante Fabricante CustoUnitario PrecoUnitario CodigoPostal Cidade Estado Regiao Distrito Pais filename Ano Mes Email Nome TotalVendas 577 2011-04-29 74362 1 Maximus UC-42 Urban Convenience 7 VanArsdel 74.73 102.37 95337 Manteca CA West District #36 USA dados_2011.csv 2011 4 adam.byers@xyza.com Adam Byers 102.37 577 2011-04-25 67126 1 Maximus UC-42 Urban Convenience 7 VanArsdel 74.73 102.37 95376 Tracy CA West District #36 USA dados_2011.csv 2011 4 sharon.alvarado@xyza.com Sharon Alvarado 102.37 577 2011-04-23 267821 1 Maximus UC-42 Urban Convenience 7 VanArsdel 74.73 102.37 94515 Calistoga CA West District #36 USA dados_2011.csv 2011 4 hall.lester@xyza.com Hall Lester 102.37 577 2011-04-20 117308 1 Maximus UC-42 Urban Convenience 7 VanArsdel 74.73 102.37 85282 Tempe AZ West District #39 USA dados_2011.csv 2011 4 rhea.thompson@xyza.com Rhea Thompson 102.37 577 2011-04-17 32630 1 Maximus UC-42 Urban Convenience 7 VanArsdel 74.73 102.37 85308 Glendale AZ West District #39 USA dados_2011.csv 2011 4 jordan.solis@xyza.com Jordan Solis 102.37 577 2011-04-30 34828 1 Maximus UC-42 Urban Convenience 7 VanArsdel 74.73 102.37 87121 Albuquerque NM West District #39 USA dados_2011.csv 2011 4 sydney.erickson@xyza.com Sydney Erickson 102.37 577 2011-04-29 236017 1 Maximus UC-42 Urban Convenience 7 VanArsdel 74.73 102.37 59828 Corvallis MT West District #33 USA dados_2011.csv 2011 4 mollie.duffy@xyza.com Mollie Duffy 102.37 577 2011-04-14 77678 1 Maximus UC-42 Urban Convenience 7 VanArsdel 74.73 102.37 59901 Kalispell MT West District #33 USA dados_2011.csv 2011 4 ingrid.dawson@xyza.com Ingrid Dawson 102.37 577 2011-04-07 120141 1 Maximus UC-42 Urban Convenience 7 VanArsdel 74.73 102.37 83687 Nampa ID West District #33 USA dados_2011.csv 2011 4 regan.patton@xyza.com Regan Patton 102.37 577 2011-04-14 190587 1 Maximus UC-42 Urban Convenience 7 VanArsdel 74.73 102.37 99501 Anchorage AK West District #34 USA dados_2011.csv 2011 4 cally.houston@xyza.com Cally Houston 102.37 577 2011-04-21 151114 1 Maximus UC-42 Urban Convenience 7 VanArsdel 74.73 102.37 89103 Las Vegas NV West District #38 USA dados_2011.csv 2011 4 taylor.ratliff@xyza.com Taylor Ratliff 102.37 625 2011-04-07 92442 1 Maximus UC-90 Urban Convenience 7 VanArsdel 98.46 134.87 44281 Wadsworth OH East District #14 USA dados_2011.csv 2011 4 clayton.chaney@xyza.com Clayton Chaney 134.87 629 2011-04-19 246840 1 Maximus UC-94 Urban Convenience 7 VanArsdel 60.52 82.90 20001 Washington DC East District #07 USA dados_2011.csv 2011 4 malik.keith@xyza.com Malik Keith 82.90 629 2011-04-30 107515 1 Maximus UC-94 Urban Convenience 7 VanArsdel 60.52 82.90 20151 Chantilly VA East District #07 USA dados_2011.csv 2011 4 risa.odonnell@xyza.com Risa Odonnell 82.90 601 2011-04-19 88942 1 Maximus UC-66 Urban Convenience 7 VanArsdel 95.79 131.22 15905 Johnstown PA East District #13 USA dados_2011.csv 2011 4 renee.bradford@xyza.com Renee Bradford 131.22 662 2011-04-02 158781 1 Maximus UC-27 Urban Convenience 7 VanArsdel 61.59 84.37 46341 Hebron IN East District #17 USA dados_2011.csv 2011 4 ezra.mcfarland@xyza.com Ezra Mcfarland 84.37 629 2011-04-06 281606 1 Maximus UC-94 Urban Convenience 7 VanArsdel 60.52 82.90 15510 Somerset PA East District #13 USA dados_2011.csv 2011 4 gwendolyn.french@xyza.com Gwendolyn French 82.90 689 2011-04-26 245264 1 Maximus UC-54 Urban Convenience 7 VanArsdel 15.31 20.97 1337 Bernardston MA East District #02 USA dados_2011.csv 2011 4 yuli.herrera@xyza.com Yuli Herrera 20.97 629 2011-04-15 155830 1 Maximus UC-94 Urban Convenience 7 VanArsdel 60.52 82.90 60467 Orland Park IL Central District #31 USA dados_2011.csv 2011 4 rashad.harrison@xyza.com Rashad Harrison 82.90 627 2011-04-13 118734 1 Maximus UC-92 Urban Convenience 7 VanArsdel 66.93 91.69 27804 Rocky Mount NC East District #08 USA dados_2011.csv 2011 4 joelle.williamson@xyza.com Joelle Williamson 91.69 639 2011-04-30 107521 1 Maximus UC-04 Urban Convenience 

In [0]:
# Particionamento por ano e mês para otimizar consultas baseadas em data, com recomendação de tamanho de arquivo

df_silver.withColumn("Ano", year("Data")) \
         .withColumn("Mes", month("Data")) \
         .write.option("maxRecordsPerFile", 50000) \
         .partitionBy("Ano", "Mes") \
         .format("parquet") \
         .mode("overwrite") \
         .save(silver_path)
#Contagem de registros
df_silver.count()

112202

### Limpando a Memória

In [0]:
import gc
gc.collect()

4412

In [0]:
del df_bronze
del df_silver